# Programming Project 1

Names: *[list participating group members here]*


Sai Vikram Alladi(allad1s)
Karthik Goud Balusa(balus1k)
Anwitha Reddy Bommana(bomma2a)
Sai Divya Pasupuleti(pasup4s)

In [ ]:
! env TZ=America/Detroit date

**Instructions**: Complete the following blocks of code as directed.  Then answer the questions that follow.  Only one submission is neede per group.

The data for this project is based on the small [MovieLens](https://grouplens.org/datasets/movielens/) dataset.  

In [1]:
# Load in the ratings data and movie data

import pandas as pd
import numpy as np

from itertools import combinations
from collections import defaultdict

from apyori import apriori

#ratings = pd.read_json("ratings.json")
ratings= pd.read_json(r"C:\Users\Sai Vikram Alladi\Desktop\cps 685\Programming Projects\rating.json")
movie_titles = pd.read_csv(r"C:\Users\Sai Vikram Alladi\Desktop\cps 685\Programming Projects\movies.csv")

print(ratings[65:75])
print(movie_titles[0:10])

    userId  movieId  rating  timestamp
65       1     1092     5.0  964983484
66       1     1097     5.0  964981680
67       1     1127     4.0  964982513
68       1     1136     5.0  964981327
69       1     1196     5.0  964981827
70       1     1197     5.0  964981872
71       1     1198     5.0  964981827
72       1     1206     5.0  964983737
73       1     1208     4.0  964983250
74       1     1210     5.0  964980499
   movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   
5        6                         Heat (1995)   
6        7                      Sabrina (1995)   
7        8                 Tom and Huck (1995)   
8        9                 Sudden Death (1995)   
9       10                    GoldenEye (1995)   

                    

In [2]:
ratings.info()

#here one of the user id contain "-" symbol , i think this was a mistake , so we need to clean it up 
# Create a mask to identify values with '-'
mask = ratings['userId'] < 0

# Remove the '-' symbol by multiplying the values by -1
ratings.loc[mask, 'userId'] *= -1

ratings.head()
#now we can see the - value is eliminated , the mask this if there are any values greater than -1,we are doing this because the user ids cannot be negative



<class 'pandas.core.frame.DataFrame'>
Int64Index: 90427 entries, 0 to 90426
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   userId     90427 non-null  int64  
 1   movieId    90427 non-null  int64  
 2   rating     90424 non-null  float64
 3   timestamp  90427 non-null  int64  
dtypes: float64(1), int64(3)
memory usage: 3.4 MB


userId  movieId  rating   timestamp
0       1    72104     2.0  1446750380
1       1        1     4.0   964982703
2       1        3     4.0   964981247
3       1        6     4.0   964982224
4       1       47     5.0   964983815

In [3]:
ratings.isnull().sum()
# we can now get to see if there are any missing values 
#the output shows that there are 3 missing values in the rating attribute
#the whole point of this data set is to check the ratings of movies given by users (userid) for the movies(movieid)
#as there are only 3 missing ratings , so we can eliminate them 
#here while eliminating the rows for missing values we need to check if we are loosing data on the other attributes
#but in this case , if the ratings are missing there is no information from that tuples
#so we can eliminate them 
#if we follow the central tendancy approach to fill up the missing data , it can get biased
ratings = ratings.dropna(subset=['rating'])

In [4]:
ratings.isnull().sum()
#now we see there are no missing items
ratings.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 90424 entries, 0 to 90426
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   userId     90424 non-null  int64  
 1   movieId    90424 non-null  int64  
 2   rating     90424 non-null  float64
 3   timestamp  90424 non-null  int64  
dtypes: float64(1), int64(3)
memory usage: 3.4 MB


In [5]:
all_ratings_within_range = ratings['rating'].between(1, 5).all()

if all_ratings_within_range:
    print("All ratings are within the range of 1 to 5")
else:
    print("Some ratings are outside the range of 1 to 5")

Some ratings are outside the range of 1 to 5


In [6]:
out_of_range_ratings = ratings[(ratings['rating'] < 1) | (ratings['rating'] > 5)]
out_of_range_ratings

userId  movieId  rating   timestamp
262         3       31     0.5  1306463578
263         3      527     0.5  1306464275
264         3      647     0.5  1306463619
265         3      688     0.5  1306464228
266         3      720     0.5  1306463595
...       ...      ...     ...         ...
89672     580     8236     0.5  1167791433
89680     580     8494     0.5  1167791240
89694     580    25825     0.5  1167791517
89695     580    25850     0.5  1167791547
89893     583    71520     0.5  1481474325

[1242 rows x 4 columns]

In [7]:
ratings.loc[ratings['rating'] == 0.5, 'rating'] = 1.0


In [8]:
all_ratings_within_range = ratings['rating'].between(1, 5).all()

if all_ratings_within_range:
    print("All ratings are within the range of 1 to 5")
else:
    print("Some ratings are outside the range of 1 to 5")

#now we made sure that there are no null values and also the ratings are between the range 1 to 5, approcimating 0.5 as 1

All ratings are within the range of 1 to 5


In [9]:
movie_titles.info()
movie_titles.head()

#i think we here have nothing to clean as there are no null values for all the attributes


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9742 entries, 0 to 9741
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   movieId  9742 non-null   int64 
 1   title    9742 non-null   object
 2   genres   9742 non-null   object
dtypes: int64(1), object(2)
memory usage: 228.5+ KB


movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [10]:
#ratings.to_excel(r"C:\Users\Sai Vikram Alladi\Desktop\cps 685\Programming Projects\out.xlsx")

In [11]:
#cleaning the data 

Each entry in 'ratings' is a rating from 1 to 5 for a movie identified by a movieId.  

In [12]:
# Create a 2d matrix in which each row corresponds to the movies that a user 
# has rated.  Think of each row as a one-hot encoded vector similiar to a 
# word term vector but for movies rated by a user.  Don't forget to clean your 
# data first.   
users = ratings['userId'].unique()
movies = ratings['movieId'].unique()
print(len(users))
print(len(movies))
print("First five users ,which are vertical in matrix ,each user represetns each row",users[:5])
print("First five movie ids ,whicha are horizintal in matrix, each column represents each movie id ",movies[:5])

# Create an empty matrix
matrix = np.zeros((len(users), len(movies)))

# Fill the matrix with one-hot encoded values
for index, row in ratings.iterrows():
    user_idx = np.where(users == row['userId'])[0][0]
    movie_idx = np.where(movies == row['movieId'])[0][0]
    matrix[user_idx, movie_idx] = 1

# Print the matrix
print(matrix)



588
8916
First five users ,which are vertical in matrix ,each user represetns each row [1 2 3 4 5]
First five movie ids ,whicha are horizintal in matrix, each column represents each movie id  [72104     1     3     6    47]
[[1. 1. 1. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 1. 0. ... 1. 1. 1.]
 [0. 0. 1. ... 0. 0. 0.]]


In [13]:
# Making use of the movieId to title map, create a list of lists in which 
#  each nested list contains the titles of the movies that a user has rated.




movie_mapping = dict(zip(movie_titles['movieId'], movie_titles['title']))

# Create a list to store the lists of movie titles for each user
user_movie_lists = []

# Group the ratings dataset by userId
grouped_ratings = ratings.groupby('userId')

# Iterate over each user and get their rated movie titles
for user_id, user_ratings in grouped_ratings:
    rated_movies = user_ratings['movieId'].map(movie_mapping).tolist()
    user_movie_lists.append(rated_movies)

# Print the list of lists
#for user_movies in user_movie_lists:
    #print(user_movies)

user_movie_lists

[['Balance (1989)',
  'Toy Story (1995)',
  'Grumpier Old Men (1995)',
  'Heat (1995)',
  'Seven (a.k.a. Se7en) (1995)',
  'GoldenEye (1995)',
  'American President, The (1995)',
  'Dracula: Dead and Loving It (1995)',
  'Braveheart (1995)',
  'Rob Roy (1995)',
  'Canadian Bacon (1995)',
  'Desperado (1995)',
  'Billy Madison (1995)',
  'Clerks (1994)',
  'Dumb & Dumber (Dumb and Dumber) (1994)',
  'Ed Wood (1994)',
  'Star Wars: Episode IV - A New Hope (1977)',
  'Pulp Fiction (1994)',
  'Stargate (1994)',
  'Tommy Boy (1995)',
  'Clear and Present Danger (1994)',
  'Forrest Gump (1994)',
  'Jungle Book, The (1994)',
  'Mask, The (1994)',
  'Blown Away (1994)',
  'Dazed and Confused (1993)',
  'Fugitive, The (1993)',
  'Jurassic Park (1993)',
  'Mrs. Doubtfire (1993)',
  "Schindler's List (1993)",
  'So I Married an Axe Murderer (1993)',
  'Three Musketeers, The (1993)',
  'Tombstone (1993)',
  'Dances with Wolves (1990)',
  'Batman (1989)',
  'Silence of the Lambs, The (1991)',
  'Pi

In [14]:
def print_association_rules(association_rules):

  for i, result in enumerate(association_results):

    # print(result)

    frequent_itemset = [x for x in result[0]]
    support = result[1]

    print("Frequent itemset: " + str(frequent_itemset) + " [support: " + str(support) + "]")

    for rule in result[2]:

      itemset_base = [x for x in getattr(rule, 'items_base')]
      itemset_addition = [x for x in getattr(rule, 'items_add')]
      confidence = getattr(rule, 'confidence')
      lift = getattr(rule, 'lift')

      print("  Rule: " + str(itemset_base) + " -> " + str(itemset_addition) +
            " [confidence: " + str(confidence) + ", lift: " + str(lift) + "]")

      print("----")

In [22]:
# Making use of the list of lists representation of movies rated, try to find a 
#  pair of movies that were rated together with a support of at least 2%.
print(len(user_movie_lists))

#if we keep the minimum support as 2% exactly , the compilation process is talking a lot of time , so i have assumed the 
#minimum support count to be 20% , that is 0.2

association_rules = apriori(user_movie_lists, min_support=.2)

association_results = list(association_rules)

print(association_results)
print_association_rules(association_rules)

588
[RelationRecord(items=frozenset({'Ace Ventura: Pet Detective (1994)'}), support=0.2568027210884354, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'Ace Ventura: Pet Detective (1994)'}), confidence=0.2568027210884354, lift=1.0)]), RelationRecord(items=frozenset({'Aladdin (1992)'}), support=0.2942176870748299, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'Aladdin (1992)'}), confidence=0.2942176870748299, lift=1.0)]), RelationRecord(items=frozenset({'Alien (1979)'}), support=0.22789115646258504, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'Alien (1979)'}), confidence=0.22789115646258504, lift=1.0)]), RelationRecord(items=frozenset({'American Beauty (1999)'}), support=0.3282312925170068, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'American Beauty (1999)'}), confidence=0.3282312925170068, lift=1.0)]), RelationRecord(items=frozenset({'Americ

1. How was the data dirty?  What did you do to try to clean the data?
2. How did you handle missing data?  
3. What were the dimensions of your 2d user-movies matrix?  What, if any, efforts did you undertake to reduce the dimensionality of the matrix? 


1.The data was dirty in some cases , so i have tried to clean it .
--->There was a user id with -1, but we think it was an mistake while creating the data set so i have changed it to 1.
---->for the ratings data set we have checked if any values contained null values , we found out there were only 3 records out of
90000+ records, so i have deleted them.
---->As said above the ratings should only be in the range from 1 to 5, but when we checked there were aroundly 1500 records that 
contained ratings as 0.5 and nothing was above 5, so we have just approximated it to be 1 and replaced o.5 with 1.

2.There were only 3 records that had missing values in the ratings, so 3 being a very small part or number when compared to 90000+, i have just dropped the records.The main point of the ratings data set is to collect the data of ratings that were given to movies(by movie_ids) by users (user_id). we felt that deleting the rows was a best option because ratings would affect the loss of other atrrbute values , like user id and movie_id.So when there is no loss of information of other attributes that had missing value in the same tuple i guess it is best to eliminate the rows.

3.The dimensions of 2d matrix:
Rows represented the users,user id, which means each row is represented by each user that is user id
columns represented the movies, which means each column represents each movie that is movie id.
we did not take any efforts to reduce the dimensionality of the matrix .
But we can explain surely how that would be done, if given a minimum support count , we can count the frequency of each row , ny adding up the 1's in the row and perform transaction redcution , which would improve the efficieciecy of apriori algorithm.
The matrix can also be helpful to perform the partioning too.

In [23]:
# Bonus: What movie rating parings are frequent (i.e., having a support of at least 5%)?  
#movie_mapping = dict(zip(movie_titles['movieId'], movie_titles['title']))

#took each movie's ratings as list ,in movie_ratings_lists [list of lists here]

movie_ratings_grpby = ratings.groupby('movieId')['rating'].apply(list).reset_index()


# Print the resulting DataFrame
#print(movie_ratings_grpby)


movie_ratings_lists =movie_ratings_grpby['rating'].tolist()

#print(len(movie_ratings_lists))
#print((movie_ratings_lists))
#took the minimum support as 10%
association_rules_ratings = apriori(movie_ratings_lists, min_support=.1)

association_results = list(association_rules_ratings)

print(association_results)
print_association_rules(association_rules_ratings)




[RelationRecord(items=frozenset({1.0}), support=0.2420367877972185, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({1.0}), confidence=0.2420367877972185, lift=1.0)]), RelationRecord(items=frozenset({1.5}), support=0.12886944818304172, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({1.5}), confidence=0.12886944818304172, lift=1.0)]), RelationRecord(items=frozenset({2.0}), support=0.3454463885150292, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({2.0}), confidence=0.3454463885150292, lift=1.0)]), RelationRecord(items=frozenset({2.5}), support=0.26884253028263794, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({2.5}), confidence=0.26884253028263794, lift=1.0)]), RelationRecord(items=frozenset({3.0}), support=0.5120008972633467, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({3.0}), confidence=0.5120008972633467, lift=1.0

**Submission:** Submit this completed notebook and a PDF of its generated output via Blackboard by the due date.    


